### Подключение пакетов и считывание данных

Информация про построение графиков - [plot_ly](https://plotly.com/r/3d-scatter-plots/)

In [1]:
# Библиотека для вывода 3D Графика
if (!requireNamespace("plotly", quietly = TRUE)) {
  install.packages("plotly")
}
library(plotly) 

# Содержит функцию varImp для выявления значимости переменных
if (!requireNamespace("caret", quietly = TRUE)) {
  install.packages("caret")
}
library(caret)


# Установить текущий рабочий каталог
setwd("~/Documents/VMK/MaSP/Data")

# Факторы вляиния, подлежащие рассмотрению
VARIAB <- c("MPG_Highway", "Length", "Weight",
            "Wheelbase", "Horsepower", "Invoice", 
            "EngineSize", "Cylinders", "Origin", "Type")

# Загрузка данных из файла
data <- read.csv("CARS.csv", header=TRUE, sep=",")
data <- data[,VARIAB]

# Преобразование переменной Invoice в числовой формат
data$Invoice <- as.double(gsub("\\$", "", gsub(",", ".", data$Invoice)))
data <- na.omit(data)

Loading required package: ggplot2


Attaching package: ‘plotly’


The following object is masked from ‘package:ggplot2’:

    last_plot


The following object is masked from ‘package:stats’:

    filter


The following object is masked from ‘package:graphics’:

    layout


Loading required package: lattice



### Вспомогательные методы класса: `COOKD_outliers`, `filter_train` и `MAPE`.

$$
MAPE = \frac{1}{n} \sum{\left|\frac{Original - Predicted}{Original}\right|}
$$

In [2]:
# Находит индексы выбросов модели
COOKD_outliers <- function(data){
    model <- lm(MPG_Highway~., data=data)

    # Рассчитываем статистику Cook's distance
    cookd <- cooks.distance(model)
    attr(model, "cookd") <- cookd

    # Находим выбросы по доверительной области
    cooks_cutoff <- 4 / (nrow(data) - length(model$coefficients) - 1)
    outliers <- which(cookd > cooks_cutoff & data$Type != 'Hybrid')

    return(outliers)
}

# На основе теста TukeyHD объединяем статистически неразличимые уровни категориальных переменных
filter_train <- function(data, outliers=TRUE){

    # Условия для объединения неразличимых уровней в группы 
    cond_1<- data$Origin == 'USA' | data$Origin == 'Europe'
    cond_2<- data$Type == 'Wagon' | data$Type == 'Sedan'
    cond_3<- data$Type == 'Wagon' | data$Type == 'Sports'
    cond_4<- data$Type == 'Truck' | data$Type == 'SUV'

    # Будет содержать только статистически различные данные
    independent_data <- data

    # Преобразование неразличимых групп
    independent_data$Origin[cond_1] <- "Group1"
    independent_data$Type[cond_2] <- "Group2"
    independent_data$Type[cond_3] <- "Group3"
    independent_data$Type[cond_4] <- "Group4"
    
    if (outliers){
        # Исключаем выбросы из данных
        return(independent_data[-c(COOKD_outliers(independent_data)), ])
    }
    else {
        return(independent_data)
    }
}

# Рассчитывает  оценку качества разработанной модели
MAPE <- function(model,  test_data=NA) {
    if (all(is.na(test_data))){
        original <- model$fitted.values
        predicted <- model$model[, "MPG_Highway"]
        n <- length(original) 
        mape <- sum(abs(original - predicted) / abs(original)) / n
        # Результирующее MAPE на закрытой проверочной процедуре должно быть меньше или равно 0.065
        if (mape > 0.065) {
            warning("MAPE значение меньше 0.065. Обратите внимание на качество модели.")
        }
        cat("MAPE результирующее:")
    }
    else{
        cat("MAPE на тесте:")
        pred <- predict(model, test_data)
        orig <- test_data$MPG_Highway
        mape <- mean(abs((orig - pred)/orig))
    }
    return(round(mape,4))
}

### Основные методы класса: `fit`, `predict`, `plot`.

In [3]:
fit <- function (data) {
    train_data <- filter_train(data) 
    model <- lm(MPG_Highway ~ ., data = train_data)
    class(model) <- c('CLASS', 'lm')

    # Исключает из рассмотрения категориальные переменные, чтобы можно было построить 3D график
    remove_cat_var <- function(matrix) {
        matrix <- matrix[!apply(matrix, 1, function(x) all(grepl('Type',x) | grepl('Origin',x) )),, drop=FALSE]
        return(matrix)
    }

    # Оценка важности переменных
    var_imp <- varImp(model)
    var_imp <- var_imp[order(var_imp$Overall),,drop=FALSE]
    names_contin_var <- remove_cat_var(as.matrix(rownames(var_imp)))
    # cat(names_contin_var,'\n',names_contin_var[length(names_contin_var)]) # Отладочная печать

    # Сохранение двух наиболее значимых для вывода на графике, и сохранение значений зависимой переменной
    model$var1_name <- names_contin_var[length(names_contin_var)]
    model$var1_val <- train_data[,model$var1_name]
    model$var2_name <- names_contin_var[length(names_contin_var)-1]
    model$var2_val <- train_data[,model$var2_name]
    #print(model$imp1_var_name) # Отладочная печать
    #print(model$imp2_var_name) # Отладочная печать
    model$resp <- train_data[,'MPG_Highway']

    return (model)
}

predict.CLASS <- function (model, test_data) {
    predict.lm(model, filter_train(test_data, outliers = FALSE))
}

plot.CLASS <- function (model) {
    # Все, что касается сетки
    my_scene = list(xaxis = list(title = model$var1_name, nticks=20),
                 yaxis = list(title = model$var2_name,nticks=20),
                 zaxis = list(title = 'MPG_Highway'))
    # Все, что касается отсчетов
    my_marker = list(size = 2, color = model$resp, 
                     colorscale = c('#FFFFFF', '#000000'), showscale = TRUE)
    # Подпись цветовой шкалы
    my_annotations = list(x = 1.18,y = -0.03, 
                          text = 'MPG_Highway',
                          xref = 'paper',
                          yref = 'paper', showarrow = FALSE)
    # Построение графика
    fig <- plot_ly( x=model$var1_val,
                    y=model$var2_val,
                    z=model$resp,
                    type = 'scatter3d',
                    mode = "markers",
                    marker = my_marker,
                    width = 500, height = 500)
    
    # Кастомизация графика
    fig <- fig %>%  layout(title='Отклик от наиболее важных переменных',
                           scene=my_scene, annotations = my_annotations)
}

In [4]:
test_data <- data[c(which(data$Type != 'Sedan')),]
#test_data <- data[c(which(data$Origin != 'USA')),]
#test_data <- data
train_data <- data

model <- fit(train_data)

MAPE(model)
MAPE(model, test_data)

MAPE результирующее:

[1] 0.0602

MAPE на тесте:

[1] 0.0812

Результирующее `MAPE` показывает себя всегда лучше, так как метод `fit` удаляет выбросы из рассмотрения. На тесте `MAPE` показывает себя хуже, так как выбросы остаются в модели.

In [5]:
p<-plot(model)
embed_notebook(p)